In [1]:
def displaySS(l, n):
    res = ["." for i in range(n)]
    for (i,j) in l:
        (res[i],res[j]) = ("(",")")
    return "".join(res)

In [2]:
displaySS([(2,8),(3,7)],10)

'..((...)).'

In [3]:
def parseSS(ss):
    p = []
    res = []
    for i,c in enumerate(ss):
        if c == '(':
            p.append(i)
        elif c == ')':
            j = p.pop()
            res.append((j,i))
    return res,len(ss)

In [4]:
ss = "((.(...)))"
print(ss)
(bps,n) = parseSS(ss)
print(bps)
print(displaySS(bps, n))

((.(...)))
[(3, 7), (1, 8), (0, 9)]
((.(...)))


In [26]:
BASE_PAIRS_NUSSINOV= {
    ('A','U') : -2,
    ('U','A') : -2,
    ('G','U') : -1,
    ('U','G') : -1,
    ('G','C') : -3,
    ('C','G') : -3,
}

BASE_PAIRS_SIMPLE= {
    ('A','U') : -1,
    ('U','A') : -1,
    ('G','U') : -1,
    ('U','G') : -1,
    ('G','C') : -1,
    ('C','G') : -1,
}

BASE_PAIRS = BASE_PAIRS_SIMPLE

def countSS(s, debug=False, theta=1):
    n = len(s)
    C = [[0 for j in range(n)] for i in range(n)]
    for m in range(1,theta+2):
        for i in range(0,n-m+1):
            j = i+m-1
            C[i][j] = 1
    for m in range(theta+2,n+1):
        for i in range(0,n-m+1):
            j = i+m-1
            # Pos i left unpaired
            C[i][j] = C[i+1][j]
            # Point i paired with j
            if ((s[i],s[j]) in BASE_PAIRS) or debug:
                C[i][j] += C[i+1][j-1]
            # Point i paired with some k<j
            for k in range(i+theta+1,j):
                if ((s[i],s[k]) in BASE_PAIRS) or debug:
                    C[i][j] += C[i+1][k-1] * C[k+1][j]
    return C[0][n-1]
    
    

In [27]:
print(countSS("A"))
print(countSS("CAG"))
print(countSS("CAGU"))
print(countSS("AAAA",True))
print(countSS("AAAAAAAA",True))
print(countSS("A"*300,True))

1
2
3
4
82
52061803444227696992763169615040001719073648961856194940280665892323694439549162483440001282797405724830363311922333433449


In [28]:
import numpy as np

def fillMatrix(s, theta=3):
    n = len(s)
    C = [[np.inf for j in range(n)] for i in range(n)]
    for m in range(1,theta+2):
        for i in range(0,n-m+1):
            j = i+m-1
            C[i][j] = 0
    for m in range(theta+2,n+1):
        for i in range(0,n-m+1):
            j = i+m-1
            # Pos i left unpaired
            C[i][j] = C[i+1][j]
            # Point i paired with j
            if (s[i],s[j]) in BASE_PAIRS:
                C[i][j] = min(C[i][j], BASE_PAIRS[(s[i],s[j])] + C[i+1][j-1])
            # Point i paired with some k<j
            for k in range(i+theta+1,j):
                if ((s[i],s[k]) in BASE_PAIRS):
                    C[i][j] = min(C[i][j], BASE_PAIRS[(s[i],s[k])] + C[i+1][k-1] + C[k+1][j])
    return C

In [36]:
#print(fillMatrix("AAAAAAAA"))
C = fillMatrix("CCCCUUUUGGGGG")
for r in C:
    print(' '.join(["%3s"%(v) for v in r]))

  0   0   0   0   0   0   0   0  -1  -2  -3  -4  -5
inf   0   0   0   0   0   0   0  -1  -2  -3  -4  -4
inf inf   0   0   0   0   0   0  -1  -2  -3  -3  -4
inf inf inf   0   0   0   0   0  -1  -2  -2  -3  -3
inf inf inf inf   0   0   0   0  -1  -1  -2  -2  -3
inf inf inf inf inf   0   0   0   0  -1  -1  -2  -2
inf inf inf inf inf inf   0   0   0   0  -1  -1  -2
inf inf inf inf inf inf inf   0   0   0   0  -1  -1
inf inf inf inf inf inf inf inf   0   0   0   0   0
inf inf inf inf inf inf inf inf inf   0   0   0   0
inf inf inf inf inf inf inf inf inf inf   0   0   0
inf inf inf inf inf inf inf inf inf inf inf   0   0
inf inf inf inf inf inf inf inf inf inf inf inf   0


In [38]:
def traceback(i, j, C, s, theta=3):
    n = len(s)
    m = j-i+1
    if m < theta+2:
        return []
    else:
        # Pos i left unpaired
        if C[i][j] == C[i+1][j]:
            return traceback(i+1, j, C, s, theta)
        # Point i paired with j
        elif ((s[i],s[j]) in BASE_PAIRS) and (C[i][j] == BASE_PAIRS[(s[i],s[j])] + C[i+1][j-1]):
            return traceback(i+1, j-1, C, s, theta)+[(i,j)]
        # Point i paired with some k<j
        for k in range(i+theta+1,j):
            if ((s[i],s[k]) in BASE_PAIRS) and (C[i][j] == BASE_PAIRS[(s[i],s[k])] + C[i+1][k-1] + C[k+1][j]):
                return [(i,k)]+traceback(i+1, k-1, C, s, theta)+traceback(k+1, j, C, s, theta)
    raise(Exception("Error: Could not find suitable case during backtrack!"))


In [51]:
s = "CAGU"*40

theta = 3
n = len(s)
C = fillMatrix(s,theta=theta)
#for r in C:
#    print(' '.join(["%3s"%(v) for v in r]))
bps = traceback(0, n-1, C, s, theta=theta)
print(s)            
print(displaySS(bps, n))
print(countSS(s,theta=theta))

CAGUCAGUCAGUCAGUCAGUCAGUCAGUCAGUCAGUCAGUCAGUCAGUCAGUCAGUCAGUCAGUCAGUCAGUCAGUCAGUCAGUCAGUCAGUCAGUCAGUCAGUCAGUCAGUCAGUCAGUCAGUCAGUCAGUCAGUCAGUCAGUCAGUCAGUCAGUCAGU
..(.(..(..(...(.(..(..(...(.(..(..(...(.(..(..(...(.(..(..(...(.(..(..(...(.(..(..(...(.(..(..(...(.(..(..(...(.(..(.....)))))))))))))))))))))))))))))))))))))))
6946885915008245584817485222079604856


In [52]:
len("6946885915008245584817485222079604856")

37

In [60]:
import math

Temp = 37.

def BF(s,i,j):
    RT = 1.986*0.001*(273.15+Temp)
    return math.exp(-BASE_PAIRS[(s[i],s[j])]/RT)

def PF(s,  theta=3):
    n = len(s)
    C = [[0 for j in range(n)] for i in range(n)]
    for m in range(1,theta+2):
        for i in range(0,n-m+1):
            j = i+m-1
            C[i][j] = 1
    for m in range(theta+2,n+1):
        for i in range(0,n-m+1):
            j = i+m-1
            # Pos i left unpaired
            C[i][j] = C[i+1][j]
            # Point i paired with j
            if ((s[i],s[j]) in BASE_PAIRS):
                C[i][j] += C[i+1][j-1]*BF(s,i,j)
            # Point i paired with some k<j
            for k in range(i+theta+1,j):
                if ((s[i],s[k]) in BASE_PAIRS):
                    C[i][j] += C[i+1][k-1] * C[k+1][j]*BF(s,i,k)
    return C


In [68]:
s = "CAAAAG"
n = len(s)
Z = PF(s)
Temp = 10000000000
print(Z[0][n-1])

2.000000503524662
